# TD 1: Fairness notion examples

In this first TD we are going to manipulate some data and see the behaviour of the different fairness metrics

Environnement python3.10

In [85]:
!pip install --upgrade pip
!pip install fairlearn==0.9.0
!pip install numpy==1.25
!pip install plotly==5.15.5
!pip install scikit-learn


ERROR: Ignored the following yanked versions: 5.2.0
ERROR: Could not find a version that satisfies the requirement plotly==5.15.5 (from versions: 0.2, 0.3, 0.4, 0.5, 0.5.1, 0.5.2, 0.5.3, 0.5.4, 0.5.5, 0.5.6, 0.5.7, 0.5.8, 0.5.9, 0.5.10, 0.5.11, 0.5.12, 0.5.13, 1.0.0, 1.0.1, 1.0.2, 1.0.3, 1.0.4, 1.0.5, 1.0.6, 1.0.7, 1.0.8, 1.0.9, 1.0.10, 1.0.11, 1.0.12, 1.0.13, 1.0.14, 1.0.15, 1.0.16, 1.0.17, 1.0.18, 1.0.19, 1.0.20, 1.0.21, 1.0.22, 1.0.23, 1.0.24, 1.0.25, 1.0.26, 1.0.27, 1.0.28, 1.0.29, 1.0.30, 1.0.31, 1.0.32, 1.0.33, 1.0.34, 1.1.0, 1.1.1, 1.1.2, 1.1.3, 1.1.4, 1.2.0, 1.2.1, 1.2.2, 1.2.3, 1.2.4, 1.2.6, 1.2.7, 1.2.8, 1.2.9, 1.3.0, 1.3.1, 1.3.2, 1.4.0, 1.4.1, 1.4.2, 1.4.3, 1.4.4, 1.4.5, 1.4.7, 1.4.9, 1.4.10, 1.4.11, 1.4.12, 1.4.13, 1.4.14, 1.5.0, 1.6.4, 1.6.6, 1.6.7, 1.6.8, 1.6.9, 1.6.10, 1.6.11, 1.6.12, 1.6.13, 1.6.14, 1.6.15, 1.6.16, 1.6.17, 1.6.19, 1.7.0, 1.7.1, 1.7.2, 1.7.3, 1.7.4, 1.7.5, 1.7.6, 1.7.7, 1.7.9, 1.8.0, 1.8.1, 1.8.2, 1.8.3, 1.8.4, 1.8.5, 1.8.6, 1.8.8, 1.8.11, 1.8.12, 1.9.0

In [2]:
!python --version

Python 3.10.12



## Objectives


 1. Study the data, the distribution of each feature and its relation to the target.

 2. Highlight some bias present in the data

 3. Learn a basic machine learning model using logistic regression

 4. Compute the confusion matrix and different fairness metrics

## Dataset: Diabetes 130-Hospitals


https://fairlearn.org/main/api_reference/generated/fairlearn.datasets.fetch_diabetes_hospital.html

Ce dataset contient 101,766 lignes chacunes concernant un patient hospitalisé pour du diabètes sur une durée allant de 1 à 14 jours. Les données ont été récoltées sur 10 ans et 130 hopitaux différents. Chaque donnée possède 25 caractéristiques concernant des informations médicales, mais aussi demographiques, enfin la colonne 'readmitted' indique si le patient a été réadmis, et si oui s'il l'a été dans les 30jours ou après. Cette colonne est binarisée en deux autres 'readmit_30_days' (True si réadmis dans les 30 jours, False sinon) et 'readmitted' ( True si réadmis, False sinon).

Nous utiliserons en label/vérité, la colonne 'readmit_30_days'.

Nous allons simplifier en ne considérant qu'un sous-ensemble de 14 des caractéristiques fournies:
age, gender, race, time_in_hospital, num_lab_procedures, num_procedures, num_medications, number_diagnoses, max_glu_serum, A1Cresult, insulin, had_emergency, had_inpatient_days, had_outpatient_days





## Download and simplify the dataset

In [8]:
import numpy as np
import fairlearn
np.__version__, fairlearn.__version__

('1.25.0', '0.9.0', '0.5.0')

In [9]:
from fairlearn.datasets import fetch_diabetes_hospital
dataset = fetch_diabetes_hospital()

In [69]:
selection = [
    "age",
    "gender",
    "race",
    "time_in_hospital",
    "num_lab_procedures",
    "num_procedures",
    "num_medications",
    "number_diagnoses",
    "max_glu_serum",
    "A1Cresult",
    "insulin",
    "had_emergency",
    "had_inpatient_days",
    "had_outpatient_days"]
df = dataset.data[selection].copy(deep=True)
label = 'readmit_30_days'
df[label] = dataset.target
# We transform boolean into integer, False=>0, True=>1
df.had_emergency = df.had_emergency.replace({"True":1, "False":0})
df.had_inpatient_days = df.had_inpatient_days.replace({"True":1, "False":0})
df.had_outpatient_days = df.had_outpatient_days.replace({"True":1, "False":0})
df

age  gender             race  time_in_hospital  \
0       30 years or younger  Female        Caucasian                 1   
1       30 years or younger  Female        Caucasian                 3   
2       30 years or younger  Female  AfricanAmerican                 2   
3               30-60 years    Male        Caucasian                 2   
4               30-60 years    Male        Caucasian                 1   
...                     ...     ...              ...               ...   
101761        Over 60 years    Male  AfricanAmerican                 3   
101762        Over 60 years  Female  AfricanAmerican                 5   
101763        Over 60 years    Male        Caucasian                 1   
101764        Over 60 years  Female        Caucasian                10   
101765        Over 60 years    Male        Caucasian                 6   

        num_lab_procedures  num_procedures  num_medications  number_diagnoses  \
0                       41               0                1                 1   
1                       59               0               18                 9   
2                       11               5               13                 6   
3                       44               1               16                 7   
4                       51               0                8                 5   
...                    ...             ...              ...               ...   
101761                  51               0               16                 9   
101762                  33               3               18                 9   
101763                  53               0                9                13   
101764                  45               2               21                 9   
101765                  13               3                3                 9   

       max_glu_serum A1Cresult insulin had_emergency had_inpatient_days  \
0               None      None      No             0                  0   
1               None      None      Up             0                  0   
2               None      None      No             0                  1   
3               None      None      Up             0                  0   
4               None      None  Steady             0                  0   
...              ...       ...     ...           ...                ...   
101761          None        >8    Down             0                  0   
101762          None      None  Steady             0                  1   
101763          None      None    Down             0                  0   
101764          None      None      Up             0                  1   
101765          None      None      No             0                  0   

       had_outpatient_days  readmit_30_days  
0                        0                0  
1                        0                0  
2                        1                0  
3                        0                0  
4                        0                0  
...                    ...              ...  
101761                   0                0  
101762                   0                0  
101763                   1                0  
101764                   0                0  
101765                   0                0  

[101766 rows x 15 columns]

## Part 1: Data Analysis

### Question1 : Count the number of positive and negative label

In [46]:
df.readmit_30_days.value_counts()

readmit_30_days
0    90409
1    11357
Name: count, dtype: int64

Now we look at the different features.
First the numerical features

### Question2: Display the distribution of the numerical features and compute their correlation with the target

In [47]:
def Compute_correlation(cola, colb):
  return np.corrcoef(df[cola].values, df[colb].values)[0][1]

In [48]:
df.dtypes

age                    object
gender                 object
race                   object
time_in_hospital        int64
num_lab_procedures      int64
num_procedures          int64
num_medications         int64
number_diagnoses        int64
max_glu_serum          object
A1Cresult              object
insulin                object
had_emergency           int64
had_inpatient_days      int64
had_outpatient_days     int64
readmit_30_days         int64
dtype: object

In [55]:
# Check that there is not NaN values
for column in df.columns:
  print(column, df[column].isnull().values.any())

age False
gender False
race False
time_in_hospital False
num_lab_procedures False
num_procedures False
num_medications False
number_diagnoses False
max_glu_serum False
A1Cresult False
insulin False
had_emergency False
had_inpatient_days False
had_outpatient_days False
readmit_30_days False


In [49]:
numerical_features = list(df.select_dtypes(include=np.number).columns)
numerical_features

['time_in_hospital',
 'num_lab_procedures',
 'num_procedures',
 'num_medications',
 'number_diagnoses',
 'had_emergency',
 'had_inpatient_days',
 'had_outpatient_days',
 'readmit_30_days']

In [70]:
for num_feature in numerical_features:
  print(num_feature, Compute_correlation(label, num_feature))

time_in_hospital 0.04419941845744675
num_lab_procedures 0.0203636025675424
num_procedures -0.01222693425174525
num_medications 0.03843182216599565
number_diagnoses 0.04952421190568102
had_emergency 0.061355221109086595
had_inpatient_days 0.12171644068564676
had_outpatient_days 0.03476246753801765
readmit_30_days 1.0


Then we consider the categorical features.

### Question3: Display histogram of categorical distribution by label for each categorical features.

In [81]:
categorical_features = list(set(df.columns)-set(numerical_features))
categorical_features

['A1Cresult', 'insulin', 'race', 'max_glu_serum', 'gender', 'age']

In [82]:
import plotly.express as px

def Display_categorical_hist(cat_feature, target):
  fig = px.histogram(df, x=cat_feature, color=target)
  fig.show()

In [83]:
for cat_feature in categorical_features:
  Display_categorical_hist(cat_feature, label)

### Question4: What are the bias highlighted by the data analysis ?

(todo, calcul de metric propre au jeu de données ??)


## Part 2: Learn a Decision Tree and study the fairness of its output

### Question5: Utiliser la technique du "one hot encoding" pour transformer chaque colonne categorielle à N catégories en N colonnes binaires

In [91]:
import pandas as pd
one_hot_data = pd.get_dummies(df[categorical_features])

In [108]:
X_numerical_features = [num_feature for num_feature in numerical_features if num_feature!=label]
df_X = pd.concat([df[X_numerical_features], one_hot_data], axis = 1)
df_X

time_in_hospital  num_lab_procedures  num_procedures  num_medications  \
0                      1                  41               0                1   
1                      3                  59               0               18   
2                      2                  11               5               13   
3                      2                  44               1               16   
4                      1                  51               0                8   
...                  ...                 ...             ...              ...   
101761                 3                  51               0               16   
101762                 5                  33               3               18   
101763                 1                  53               0                9   
101764                10                  45               2               21   
101765                 6                  13               3                3   

        number_diagnoses had_emergency had_inpatient_days had_outpatient_days  \
0                      1             0                  0                   0   
1                      9             0                  0                   0   
2                      6             0                  1                   1   
3                      7             0                  0                   0   
4                      5             0                  0                   0   
...                  ...           ...                ...                 ...   
101761                 9             0                  0                   0   
101762                 9             0                  1                   0   
101763                13             0                  0                   1   
101764                 9             0                  1                   0   
101765                 9             0                  0                   0   

        A1Cresult_>7  A1Cresult_>8  ...  max_glu_serum_>200  \
0              False         False  ...               False   
1              False         False  ...               False   
2              False         False  ...               False   
3              False         False  ...               False   
4              False         False  ...               False   
...              ...           ...  ...                 ...   
101761         False          True  ...               False   
101762         False         False  ...               False   
101763         False         False  ...               False   
101764         False         False  ...               False   
101765         False         False  ...               False   

        max_glu_serum_>300  max_glu_serum_None  max_glu_serum_Norm  \
0                    False                True               False   
1                    False                True               False   
2                    False                True               False   
3                    False                True               False   
4                    False                True               False   
...                    ...                 ...                 ...   
101761               False                True               False   
101762               False                True               False   
101763               False                True               False   
101764               False                True               False   
101765               False                True               False   

        gender_Female  gender_Male  gender_Unknown/Invalid  \
0                True        False                   False   
1                True        False                   False   
2                True        False                   False   
3               False         True                   False   
4               False         True                   False   
...               ...          ...                     ...   
101761          False         

### Question6 : Split data into train and test sets



In [120]:
from sklearn.model_selection import train_test_split
X_train, X_test, y_train, y_test = train_test_split(df_X, df[label], test_size=0.33, random_state=42)

### Question 7: Train a DecisionTreeClassifier (https://scikit-learn.org/stable/modules/tree.html#classification)

In [132]:
from sklearn import tree
clf = tree.DecisionTreeClassifier(random_state=42)
clf = clf.fit(X_train, y_train)

In [133]:
preds = clf.predict(X_test)

In [134]:
clf.score(X_test, y_test)

0.787124437959682

In [135]:
# tree.plot_tree(clf) #visualise the tree, only if max_depth<=6

### Question8: Compute the Confusion Matrix

In [136]:
from sklearn.metrics import confusion_matrix
tn, fp, fn, tp = confusion_matrix(y_test, preds).ravel()
tn, fp, fn, tp

(25821, 3996, 3153, 613)